# Read HRRR Forecast model data from Zarr 

In [1]:
from dask.distributed import Client, progress
from dask_kubernetes import KubeCluster
import xarray as xr
import numpy as np
import hvplot.xarray
import geoviews as gv
import cartopy.crs as ccrs
import fsspec
import metpy

/srv/conda/envs/notebook/lib/python3.7/site-packages/datashader/transfer_functions.py:21: FutureWarning: xarray subclass Image should explicitly define __slots__
  class Image(xr.DataArray):


In [2]:
cluster = KubeCluster()

In [3]:
cluster.scale(5);

In [4]:
cluster

In [5]:
cluster.adapt(maximum=5)
client = Client(cluster)

In [6]:
ds = xr.open_zarr(fsspec.get_mapper('s3://esip-pangeo-uswest2/pangeo/EPIC/hrrr_zarr'))

In [7]:
ds

<xarray.Dataset>
Dimensions:                                  (height_above_ground1: 1, height_above_ground3: 2, time: 90, x: 2145, y: 1377)
Coordinates:
  * height_above_ground1                     (height_above_ground1) float32 2.0
  * height_above_ground3                     (height_above_ground3) float32 10.0 80.0
    reftime                                  (time) datetime64[ns] dask.array<chunksize=(90,), meta=np.ndarray>
  * time                                     (time) datetime64[ns] 2019-09-15T23:00:00 ... 2019-09-19T16:00:00
  * x                                        (x) float32 -2763.217 ... 2681.906
  * y                                        (y) float32 -263.79062 ... 3230.8406
Data variables:
    LambertConformal_Projection              int32 ...
    Temperature_height_above_ground          (time, height_above_ground1, y, x) float32 dask.array<chunksize=(10, 1, 1377, 2145), meta=np.ndarray>
    u-component_of_wind_height_above_ground  (time, height_above_ground3, y, 

In [8]:
da  = ds.metpy.parse_cf('u-component_of_wind_height_above_ground')

In [9]:
crs = da.metpy.cartopy_crs

In [10]:
base_map = gv.tile_sources.OSM

In [11]:
windspeed = np.sqrt(ds['u-component_of_wind_height_above_ground']**2 + ds['v-component_of_wind_height_above_ground']**2)

In [12]:
windspeed.nbytes/1e9

2.1266388

In [13]:
windspeed

<xarray.DataArray (time: 90, height_above_ground3: 2, y: 1377, x: 2145)>
dask.array<sqrt, shape=(90, 2, 1377, 2145), dtype=float32, chunksize=(10, 2, 1377, 2145), chunktype=numpy.ndarray>
Coordinates:
  * height_above_ground3  (height_above_ground3) float32 10.0 80.0
    reftime               (time) datetime64[ns] 2019-09-15T23:00:00 ... 2019-09-18T22:00:00
  * time                  (time) datetime64[ns] 2019-09-15T23:00:00 ... 2019-09-19T16:00:00
  * x                     (x) float32 -2763.217 -2760.6772 ... 2681.906
  * y                     (y) float32 -263.79062 -261.25092 ... 3230.8406

In [14]:
wind_max = windspeed.max(dim='time').persist()
progress(wind_max)

VBox()

In [15]:
wind_max

<xarray.DataArray (height_above_ground3: 2, y: 1377, x: 2145)>
dask.array<nanmax-aggregate, shape=(2, 1377, 2145), dtype=float32, chunksize=(2, 1377, 2145), chunktype=numpy.ndarray>
Coordinates:
  * height_above_ground3  (height_above_ground3) float32 10.0 80.0
  * x                     (x) float32 -2763.217 -2760.6772 ... 2681.906
  * y                     (y) float32 -263.79062 -261.25092 ... 3230.8406

In [16]:
mesh = wind_max.hvplot(x='x', y='y', rasterize=True, cmap='viridis', crs=crs, width=700)

In [17]:
(base_map * mesh.opts(alpha=0.7)).opts(active_tools=['wheel_zoom', 'pan'])

/srv/conda/envs/notebook/lib/python3.7/site-packages/numba/compiler.py:602: NumbaPerformanceWarning: 
The keyword argument 'parallel=True' was specified but no transformation for parallel execution was possible.

To find out why, try turning on parallel diagnostics, see http://numba.pydata.org/numba-doc/latest/user/parallel.html#diagnostics for help.

File "../../../../srv/conda/envs/notebook/lib/python3.7/site-packages/datashader/resampling.py", line 235:
@ngjit_parallel
def _get_dimensions(src, out):
^

  self.func_ir.loc))


:DynamicMap   [height_above_ground3]
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [x,y]   (value)

In [18]:
mesh = windspeed.hvplot(x='x', y='y', rasterize=True, cmap='viridis', crs=crs, width=700)
base_map * mesh.opts(alpha=0.7)

:DynamicMap   [time,height_above_ground3]
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [x,y]   (value)